In [ ]:
import numpy as np
import individual_methods as estimate
from sklearn.linear_model import ElasticNet, ElasticNetCV, LinearRegression
import pandas as pd
from sklearn.neural_network import MLPRegressor

#read in data
data = pd.read_csv('geithner_outcome.csv')

#select the last 100 periods and then scale data by 1e-8
units = 11
periods = 476
GDP = data.values[:units,-periods:].astype(float)*1e2

#GDP growth rate
#GDP = data.values[:,-11:].astype(float)
#GDP = (GDP[:,1:]-GDP[:,:-1])/GDP[:,:-1]*1e2
#units, periods = GDP.shape


#specify the number of test and train periods
test_periods = 10
train_periods = periods-test_periods

#record RMSE of predictions by 8 methods
RMSE_test = np.zeros((units,test_periods,8))

#ensemble weights

#HR+VT restricted
ensem1_weights = np.zeros((units,2))

#HR+VT+MC restricted
ensem2_weights = np.zeros((units,3))

#HR+VT+Abadie+MC restricted
ensem3_weights = np.zeros((units,4))

#HR+VT+MC neural network
ensem4_weights = []

#to calculate correlation of predictions by different methods
Epsilon = np.zeros((units,test_periods,4))

#outcome matrix for training to obtain ensemble weights
Y = GDP[:,:-test_periods]

#matrix of RMSE for ensemble weighting
RMSE_weight = np.zeros((units,train_periods,4))

#record the regularization strengths obtained from cross validation
HR = np.zeros((units,2))
VT = np.zeros((units,2))

#for each unit, obtain weights from train periods first, then 
#apply individual and ensemble methods to test periods

#train for training periods
for current_unit in range(units):
    
    #shift current unit to the last row
    Y0 = np.roll(Y,-current_unit-1,0)
    
    #to save computation time, obtain regularization from cross-validation
    #for last period of current unit and use that for all train periods
    _, HR_alpha, HR_l1_ratio = estimate.HR(Y0,cv=True)
    _, VT_alpha, VT_l1_ratio = estimate.VT(Y0,cv=True)
    
    #record the regularization strengths obtained from cross validation
    HR[current_unit,0] = HR_alpha
    HR[current_unit,1] = HR_l1_ratio
    VT[current_unit,0] = VT_alpha
    VT[current_unit,1] = VT_l1_ratio
    
    #record predictions of individual methods and actual outcome for 
    #regression ensemble weighting
    individual_predictions = np.zeros((train_periods,4))
    actual_outcomes = np.zeros(train_periods,)
    
    for train_period in range(train_periods):
        
        #shift current train period to the last column
        Y_shift = np.roll(Y0,-train_period-1,1)
        actual_outcomes[train_period] = Y_shift[-1,-1]
        
        #obtain RMSE for ensemble weighting
        
        #METHOD-1 MC
        individual_predictions[train_period,0] = estimate.MC(Y_shift)
        
        #METHOD-2 HR
        individual_predictions[train_period,1] = estimate.HR(Y_shift,a=HR_alpha,b=HR_l1_ratio)
        
        #METHOD-3 VT
        individual_predictions[train_period,2] = estimate.VT(Y_shift,a=VT_alpha,b=VT_l1_ratio)
        
        #METHOD-4 Abadie
        individual_predictions[train_period,3] = estimate.Abadie(Y_shift)
        
        RMSE_weight[current_unit,train_period,:] = np.absolute(individual_predictions[train_period,:]-actual_outcomes[train_period])
        
    #obtain ensemble weights for regression ensemble methods
    
    #HR+VT restricted
    ensem1_weights[current_unit,:] = estimate.restricted_regression(individual_predictions[:,1:3],actual_outcomes)

    #HR+VT+MC restricted
    ensem2_weights[current_unit,:] = estimate.restricted_regression(individual_predictions[:,0:3],actual_outcomes)

    #HR+VT+Abadie+MC restricted
    ensem3_weights[current_unit,:] = estimate.restricted_regression(individual_predictions[:,0:],actual_outcomes)

    #HR+VT+MC neural net
    cv_layers = [(100,),(50,),(20,)]
    cv_alpha = [0.1,0.01,0.001,0.0001]
    
    layers, alpha = estimate.neural_net_cv(individual_predictions[:,0:3],actual_outcomes,cv_layers,cv_alpha,cv=10)
    neural_regressor = MLPRegressor(hidden_layer_sizes=layers,alpha=alpha)
    neural_regressor.fit(individual_predictions[:,0:3],actual_outcomes)
    ensem4_weights.append(neural_regressor)
 
#obtain inverse-RMSE ensemble weighting
#RMSE_weight = np.squeeze(np.sum(np.square(RMSE_weight),1))
#RMSE_weight = np.sqrt(RMSE_weight)

#inv_RMSE = np.reciprocal(RMSE_weight)
#ensem2_weights = (inv_RMSE.T/np.sum(inv_RMSE,1)).T


#predict for test periods
for test_period in range(test_periods):
    
    #select outcomes up to the current (to be predicted) period
    Y = GDP[:,:periods-test_periods+test_period+1]
    
    for current_unit in range(units):
    
        #shift current unit to the last row
        Y0 = np.roll(Y,-current_unit-1,0)
        
        #record predictions of individual methods
        individual_predictions = np.zeros(4,)
        
        #compare with actual outcome 
        actual_outcome = Y0[-1,-1]
        
        #METHOD-1 MC
        individual_predictions[0] = estimate.MC(Y0)
        
        #METHOD-2 HR
        #individual_predictions[1],_,_ = estimate.HR(Y0,cv=True)
        individual_predictions[1] = estimate.HR(Y0,a=HR[current_unit,0],b=HR[current_unit,1])
        
        #METHOD-3 VT
        #individual_predictions[2],_,_ = estimate.SC(Y0,cv=True)
        individual_predictions[2] = estimate.VT(Y0,a=VT[current_unit,0],b=VT[current_unit,1])
        
        #METHOD-4 Abadie
        individual_predictions[3] = estimate.Abadie(Y0)
        
        Epsilon[current_unit,test_period,:] = individual_predictions-actual_outcome
        
        RMSE_test[current_unit,test_period,0:4] = np.absolute(individual_predictions-actual_outcome)
        
        #ensemble-1 HR+VT restricted
        ensem_prediction = np.dot(ensem1_weights[current_unit,:],individual_predictions[1:3])
        RMSE_test[current_unit,test_period,4] = np.absolute(ensem_prediction-actual_outcome)
        
        #ensemble-2 HR+VT+MC restricted
        ensem_prediction = np.dot(ensem2_weights[current_unit,:],individual_predictions[:3])
        RMSE_test[current_unit,test_period,5] = np.absolute(ensem_prediction-actual_outcome)
        
        #ensemble-3 HR+VT+Abadie+MC restricted
        ensem_prediction = np.dot(ensem3_weights[current_unit,:],individual_predictions[0:])
        RMSE_test[current_unit,test_period,6] = np.absolute(ensem_prediction-actual_outcome)
        
        #ensemble-4 HR+VT+MC neural 
        current_neural_net = ensem4_weights[current_unit]
        ensem_prediction = current_neural_net.predict(individual_predictions[:3].reshape(1,-1))
        RMSE_test[current_unit,test_period,7] = np.absolute(ensem_prediction-actual_outcome)       

#calculate RMSE by averaging over test periods, i.e. axis 1        
RMSE_final = np.squeeze(np.sqrt(np.sum(np.square(RMSE_test),1)/test_periods))
RMSE_final = (RMSE_final.T/np.std(GDP,axis=1)).T
overall = np.sqrt(np.sum(np.square(RMSE_final),0)/units)
#med = np.median(RMSE_final,0);

RMSE_output = np.concatenate((RMSE_final,np.reshape(overall,(1,-1))))

#calculate correlation and covariance of individual methods
cov_input = np.reshape(Epsilon.transpose(),(4,-1))

covariance_matrix = np.cov(cov_input)
correlation_matrix = np.corrcoef(cov_input)

index1 = list(np.arange(units))
index1 = index1.append('mean')
columns1 = ['MC','HR','VT','Abadie','HR+VT','MC+HR+VT','MC+HR+VT+Abadie','HR+VT+MC neural']
RMSE_print = pd.DataFrame(np.around(RMSE_output,5),index=index1,columns=columns1)  

index2 = np.arange(units)
columns2 = ['MC','HR','VT','Abadie']

corr_print = pd.DataFrame(correlation_matrix,index=columns2,columns=columns2)
ensem1_print = pd.DataFrame(ensem1_weights,index=index2,columns=['HR','VT'])
ensem2_print = pd.DataFrame(ensem2_weights,index=index2,columns=['MC','HR','VT'])
ensem3_print = pd.DataFrame(ensem3_weights,index=index2,columns=['MC','HR','VT','Abadie'])
#ensem4_print = pd.DataFrame(ensem4_weights,index=index2,columns=['HR','VT','Abadie'])
    
RMSE_print.to_csv('RMSE_10.csv')
corr_print.to_csv('corr_10.csv')
ensem1_print.to_csv('ensem1_10.csv')
ensem2_print.to_csv('ensem2_10.csv')
ensem3_print.to_csv('ensem3_10.csv')
#ensem4_print.to_csv('ensem4_10.csv')

Using TensorFlow backend.


[SoftImpute] Max Singular Value of X_init = 230.766425
[SoftImpute] Iter 1: observed MAE=0.137693 rank=11
[SoftImpute] Iter 2: observed MAE=0.137693 rank=11
[SoftImpute] Iter 3: observed MAE=0.137693 rank=11
[SoftImpute] Iter 4: observed MAE=0.137694 rank=11
[SoftImpute] Iter 5: observed MAE=0.137694 rank=11
[SoftImpute] Iter 6: observed MAE=0.137694 rank=11
[SoftImpute] Iter 7: observed MAE=0.137694 rank=11
[SoftImpute] Iter 8: observed MAE=0.137694 rank=11
[SoftImpute] Iter 9: observed MAE=0.137694 rank=11
[SoftImpute] Iter 10: observed MAE=0.137694 rank=11
[SoftImpute] Iter 11: observed MAE=0.137694 rank=11
[SoftImpute] Iter 12: observed MAE=0.137695 rank=11
[SoftImpute] Iter 13: observed MAE=0.137695 rank=11
[SoftImpute] Iter 14: observed MAE=0.137695 rank=11
[SoftImpute] Iter 15: observed MAE=0.137695 rank=11
[SoftImpute] Iter 16: observed MAE=0.137695 rank=11
[SoftImpute] Iter 17: observed MAE=0.137695 rank=11
[SoftImpute] Iter 18: observed MAE=0.137695 rank=11
[SoftImpute] Iter 

[SoftImpute] Max Singular Value of X_init = 230.784466
[SoftImpute] Iter 1: observed MAE=0.137663 rank=11
[SoftImpute] Iter 2: observed MAE=0.137662 rank=11
[SoftImpute] Iter 3: observed MAE=0.137662 rank=11
[SoftImpute] Iter 4: observed MAE=0.137662 rank=11
[SoftImpute] Iter 5: observed MAE=0.137661 rank=11
[SoftImpute] Iter 6: observed MAE=0.137661 rank=11
[SoftImpute] Iter 7: observed MAE=0.137661 rank=11
[SoftImpute] Iter 8: observed MAE=0.137660 rank=11
[SoftImpute] Iter 9: observed MAE=0.137660 rank=11
[SoftImpute] Iter 10: observed MAE=0.137660 rank=11
[SoftImpute] Iter 11: observed MAE=0.137660 rank=11
[SoftImpute] Iter 12: observed MAE=0.137659 rank=11
[SoftImpute] Iter 13: observed MAE=0.137659 rank=11
[SoftImpute] Iter 14: observed MAE=0.137659 rank=11
[SoftImpute] Iter 15: observed MAE=0.137659 rank=11
[SoftImpute] Iter 16: observed MAE=0.137658 rank=11
[SoftImpute] Iter 17: observed MAE=0.137658 rank=11
[SoftImpute] Iter 18: observed MAE=0.137658 rank=11
[SoftImpute] Iter 

[SoftImpute] Iter 63: observed MAE=0.137688 rank=11
[SoftImpute] Iter 64: observed MAE=0.137688 rank=11
[SoftImpute] Iter 65: observed MAE=0.137688 rank=11
[SoftImpute] Iter 66: observed MAE=0.137688 rank=11
[SoftImpute] Iter 67: observed MAE=0.137688 rank=11
[SoftImpute] Stopped after iteration 67 for lambda=4.615180
[SoftImpute] Max Singular Value of X_init = 230.769650
[SoftImpute] Iter 1: observed MAE=0.137695 rank=11
[SoftImpute] Iter 2: observed MAE=0.137695 rank=11
[SoftImpute] Iter 3: observed MAE=0.137695 rank=11
[SoftImpute] Iter 4: observed MAE=0.137695 rank=11
[SoftImpute] Iter 5: observed MAE=0.137695 rank=11
[SoftImpute] Iter 6: observed MAE=0.137695 rank=11
[SoftImpute] Iter 7: observed MAE=0.137695 rank=11
[SoftImpute] Iter 8: observed MAE=0.137695 rank=11
[SoftImpute] Iter 9: observed MAE=0.137695 rank=11
[SoftImpute] Iter 10: observed MAE=0.137695 rank=11
[SoftImpute] Iter 11: observed MAE=0.137695 rank=11
[SoftImpute] Iter 12: observed MAE=0.137695 rank=11
[SoftImput

[SoftImpute] Iter 63: observed MAE=0.137691 rank=11
[SoftImpute] Iter 64: observed MAE=0.137691 rank=11
[SoftImpute] Iter 65: observed MAE=0.137691 rank=11
[SoftImpute] Iter 66: observed MAE=0.137691 rank=11
[SoftImpute] Iter 67: observed MAE=0.137691 rank=11
[SoftImpute] Iter 68: observed MAE=0.137691 rank=11
[SoftImpute] Stopped after iteration 68 for lambda=4.615079
[SoftImpute] Max Singular Value of X_init = 230.770453
[SoftImpute] Iter 1: observed MAE=0.137687 rank=11
[SoftImpute] Iter 2: observed MAE=0.137687 rank=11
[SoftImpute] Iter 3: observed MAE=0.137687 rank=11
[SoftImpute] Iter 4: observed MAE=0.137687 rank=11
[SoftImpute] Iter 5: observed MAE=0.137687 rank=11
[SoftImpute] Iter 6: observed MAE=0.137687 rank=11
[SoftImpute] Iter 7: observed MAE=0.137687 rank=11
[SoftImpute] Iter 8: observed MAE=0.137687 rank=11
[SoftImpute] Iter 9: observed MAE=0.137687 rank=11
[SoftImpute] Iter 10: observed MAE=0.137687 rank=11
[SoftImpute] Iter 11: observed MAE=0.137687 rank=11
[SoftImput

...

[SoftImpute] Iter 12: observed MAE=0.137702 rank=11
[SoftImpute] Iter 13: observed MAE=0.137702 rank=11
[SoftImpute] Iter 14: observed MAE=0.137702 rank=11
[SoftImpute] Iter 15: observed MAE=0.137702 rank=11
[SoftImpute] Iter 16: observed MAE=0.137702 rank=11
[SoftImpute] Iter 17: observed MAE=0.137702 rank=11
[SoftImpute] Iter 18: observed MAE=0.137702 rank=11
[SoftImpute] Iter 19: observed MAE=0.137702 rank=11
[SoftImpute] Iter 20: observed MAE=0.137702 rank=11
[SoftImpute] Iter 21: observed MAE=0.137702 rank=11
[SoftImpute] Iter 22: observed MAE=0.137702 rank=11
[SoftImpute] Iter 23: observed MAE=0.137702 rank=11
[SoftImpute] Iter 24: observed MAE=0.137702 rank=11
[SoftImpute] Iter 25: observed MAE=0.137702 rank=11
[SoftImpute] Iter 26: observed MAE=0.137702 rank=11
[SoftImpute] Iter 27: observed MAE=0.137702 rank=11
[SoftImpute] Iter 28: observed MAE=0.137702 rank=11
[SoftImpute] Iter 29: observed MAE=0.137702 rank=11
[SoftImpute] Iter 30: observed MAE=0.137702 rank=11
[SoftImpute]

[SoftImpute] Iter 88: observed MAE=0.137696 rank=11
[SoftImpute] Iter 89: observed MAE=0.137696 rank=11
[SoftImpute] Iter 90: observed MAE=0.137696 rank=11
[SoftImpute] Iter 91: observed MAE=0.137696 rank=11
[SoftImpute] Iter 92: observed MAE=0.137696 rank=11
[SoftImpute] Iter 93: observed MAE=0.137696 rank=11
[SoftImpute] Iter 94: observed MAE=0.137696 rank=11
[SoftImpute] Iter 95: observed MAE=0.137696 rank=11
[SoftImpute] Iter 96: observed MAE=0.137696 rank=11
[SoftImpute] Iter 97: observed MAE=0.137696 rank=11
[SoftImpute] Iter 98: observed MAE=0.137696 rank=11
[SoftImpute] Iter 99: observed MAE=0.137696 rank=11
[SoftImpute] Iter 100: observed MAE=0.137696 rank=11
[SoftImpute] Stopped after iteration 100 for lambda=4.615447
[SoftImpute] Max Singular Value of X_init = 230.769338
[SoftImpute] Iter 1: observed MAE=0.137693 rank=11
[SoftImpute] Iter 2: observed MAE=0.137693 rank=11
[SoftImpute] Iter 3: observed MAE=0.137693 rank=11
[SoftImpute] Iter 4: observed MAE=0.137693 rank=11
[So

[SoftImpute] Iter 49: observed MAE=0.137732 rank=11
[SoftImpute] Iter 50: observed MAE=0.137732 rank=11
[SoftImpute] Iter 51: observed MAE=0.137732 rank=11
[SoftImpute] Iter 52: observed MAE=0.137732 rank=11
[SoftImpute] Iter 53: observed MAE=0.137732 rank=11
[SoftImpute] Iter 54: observed MAE=0.137732 rank=11
[SoftImpute] Iter 55: observed MAE=0.137732 rank=11
[SoftImpute] Iter 56: observed MAE=0.137732 rank=11
[SoftImpute] Iter 57: observed MAE=0.137732 rank=11
[SoftImpute] Iter 58: observed MAE=0.137732 rank=11
[SoftImpute] Iter 59: observed MAE=0.137732 rank=11
[SoftImpute] Iter 60: observed MAE=0.137732 rank=11
[SoftImpute] Iter 61: observed MAE=0.137732 rank=11
[SoftImpute] Iter 62: observed MAE=0.137732 rank=11
[SoftImpute] Iter 63: observed MAE=0.137732 rank=11
[SoftImpute] Iter 64: observed MAE=0.137732 rank=11
[SoftImpute] Iter 65: observed MAE=0.137732 rank=11
[SoftImpute] Iter 66: observed MAE=0.137732 rank=11
[SoftImpute] Iter 67: observed MAE=0.137732 rank=11
[SoftImpute]

[SoftImpute] Iter 97: observed MAE=0.137643 rank=11
[SoftImpute] Iter 98: observed MAE=0.137643 rank=11
[SoftImpute] Iter 99: observed MAE=0.137643 rank=11
[SoftImpute] Iter 100: observed MAE=0.137643 rank=11
[SoftImpute] Stopped after iteration 100 for lambda=4.614877
[SoftImpute] Max Singular Value of X_init = 230.773590
[SoftImpute] Iter 1: observed MAE=0.137683 rank=11
[SoftImpute] Iter 2: observed MAE=0.137683 rank=11
[SoftImpute] Iter 3: observed MAE=0.137683 rank=11
[SoftImpute] Iter 4: observed MAE=0.137683 rank=11
[SoftImpute] Iter 5: observed MAE=0.137683 rank=11
[SoftImpute] Iter 6: observed MAE=0.137683 rank=11
[SoftImpute] Iter 7: observed MAE=0.137683 rank=11
[SoftImpute] Iter 8: observed MAE=0.137683 rank=11
[SoftImpute] Iter 9: observed MAE=0.137683 rank=11
[SoftImpute] Iter 10: observed MAE=0.137683 rank=11
[SoftImpute] Iter 11: observed MAE=0.137683 rank=11
[SoftImpute] Iter 12: observed MAE=0.137683 rank=11
[SoftImpute] Iter 13: observed MAE=0.137683 rank=11
[SoftImp

[Parallel(n_jobs=2)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:   15.3s
[Parallel(n_jobs=2)]: Done 120 out of 120 | elapsed: 173.1min finished
c:\users\zhaon\appdata\local\programs\python\python36\lib\site-packages\sklearn\model_selection\_search.py:841: DeprecationWarning: The default of the `iid` parameter will change from True to False in version 0.22 and will be removed in 0.24. This will change numeric results when test-set sizes are unequal.
  DeprecationWarning)
c:\users\zhaon\appdata\local\programs\python\python36\lib\site-packages\sklearn\neural_network\multilayer_perceptron.py:562: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
